In [1]:
import sys

# Define the branch you want to install from
branch = "master"

# Install dependencies whether in Colab or not
#!pip install --quiet --upgrade jsonschema
#!pip install --quiet git+https://github.com/yoseflab/hotspot@$branch
#!pip install --quiet scanpy
#!pip install --quiet muon
#!pip install --quiet mplscience

In [ ]:
import warnings; warnings.simplefilter('ignore')

import hotspot
import scanpy as sc
# import muon as mu

import numpy as np
import mplscience

import matplotlib.pyplot as plt

import pickle

import pandas as pd

In [ ]:
samples = ['T12','T3','T4','T21','T23','T11','T18','T26','T16','T17','T20','T15','T13','T19','T24','T22']

# Loop through each sample
for sample in samples:
    
    print(f"Processing sample: {sample}")
    
    # Load the .h5ad file for the current sample
    adata_cd4 = sc.read(f'/gpfs/data/yanailab/projects/dl4564/PTOI/objects/{sample}.Malignant.h5ad')

    # Perform preprocessing and PCA
    adata_cd4.layers["counts"] = adata_cd4.raw.X
    sc.pp.filter_genes(adata_cd4, min_cells=1)
    sc.pp.normalize_total(adata_cd4)
    sc.pp.log1p(adata_cd4)
    adata_cd4.layers["log_normalized"] = adata_cd4.X.copy()
    sc.pp.scale(adata_cd4)
    sc.tl.pca(adata_cd4)

    with mplscience.style_context():
        sc.pl.pca_variance_ratio(adata_cd4)

    # Rerun PCA with fewer components
    sc.tl.pca(adata_cd4, n_comps=8)

    # Create the Hotspot object and the neighborhood graph
    adata_cd4.layers["counts_csc"] = adata_cd4.layers["counts"].tocsc()
    hs = hotspot.Hotspot(
        adata_cd4,
        layer_key="counts_csc",
        model='danb',
        latent_obsm_key="X_pca",
        umi_counts_obs_key="nCount_RNA"
    )

    hs.create_knn_graph(weighted_graph=False, n_neighbors=50)
    hs_results = hs.compute_autocorrelations(jobs=4)

    # Sort by 'Z' and select the top 2000 genes
    hs_genes = hs_results.sort_values('Z', ascending=False).head(2000).index

    # Exclude genes that start with 'mt-', 'Rpl', or 'Rps'
    exclude_patterns = ['^mt-', '^Rpl', '^Rps']
    for pattern in exclude_patterns:
        hs_genes = hs_genes[~hs_genes.str.contains(pattern, regex=True)]

    # Compute pairwise local correlations between the selected genes
    lcz = hs.compute_local_correlations(hs_genes, jobs=4)

    # Create modules based on the local correlations
    modules = hs.create_modules(
        min_gene_threshold=30, core_only=True, fdr_threshold=0.05
    )

    # Plot local correlations
    hs.plot_local_correlations(vmin=-12, vmax=12)
    plt.savefig(f"/gpfs/data/yanailab/projects/dl4564/PTOI/modules/Malignant/{sample}_hotspot_local_correlations.png")

    # Save the modules and plot for the current sample
    modules.to_csv(f'/gpfs/data/yanailab/projects/dl4564/PTOI/modules/Malignant/{sample}_hotspot.modules.csv', header=True)
    
    # Save the gene - gene zscore correlation matrix!
    hs.local_correlation_z.to_csv(f"/gpfs/data/yanailab/projects/dl4564/PTOI/modules/Malignant/{sample}_zscore_correlation_hotspot.csv")
    
    # Save the Hotspot object for the current sample
with open(f'/gpfs/data/yanailab/projects/dl4564/PTOI/objects/{sample}_hotspot.pkl', 'wb') as f:
    pickle.dump(hs, f)
